In [1]:
import pandas as pd
from pathlib import Path
from sqlalchemy import create_engine, text

import folium
from folium.plugins import MarkerCluster
import requests
import json

# Create a reference to the file.
database_path = Path("../Resources/heart_disease.db")

In [2]:
# Create an engine to connect to the SQL database
conn = create_engine(f"sqlite:///{database_path}").connect()


In [3]:
# Query All Records in the the Database
query = text("SELECT * FROM clean_Heart_Disease")
data = conn.execute(query)

for record in data:
    print(record)

('AK', 'Kenai Peninsula', 'County', '165.1', 'Male', 'Hispanic', '02122', '60.19326297', '-150.2807443')
('AL', 'Walker County', 'County', '109', 'Overall', 'Hispanic', '01127', '33.81022639', '-87.29707047')
('AL', 'St. Clair County', 'County', '90', 'Overall', 'Asian', '01115', '33.71606539', '-86.31496031')
('AR', 'Yell County', 'County', None, 'Female', 'Asian', '05149', '35.00586398', '-93.40167591')
('AS', 'American Samoa County', 'County', None, 'Male', 'Black', '60000', '-14.30175426', '-170.7194738')
('FL', 'Polk County', 'County', '180.2', 'Female', 'Hispanic', '12105', '27.9460498', '-81.69939066')
('GA', 'Forsyth County', 'County', '133.5', 'Overall', 'Asian', '13117', '34.2283909', '-84.12468503')
('GA', 'DeKalb County', 'County', '368.4', 'Male', 'More than one race', '13089', '33.77205395', '-84.22067829')
('IL', 'McHenry County', 'County', '217.4', 'Male', 'Hispanic', '17111', '42.32380258', '-88.45396096')
('IL', 'DuPage County', 'County', '149', 'Male', 'More than one

('GA', 'Camden County', 'County', None, 'Overall', 'More than one race', '13039', '30.93036103', '-81.68070853')
('CO', 'Elbert County', 'County', '168.2', 'Female', 'Overall', '08039', '39.28030152', '-104.1306718')
('AR', 'Columbia County', 'County', None, 'Male', 'More than one race', '05027', '33.21644457', '-93.21637984')
('GA', 'Clarke County', 'County', '315.6', 'Overall', 'White', '13059', '33.95588157', '-83.36843056')
('GA', 'Grady County', 'County', '568.7', 'Male', 'Black', '13131', '30.87681982', '-84.22831529')
('CO', 'Prowers County', 'County', '337.9', 'Overall', 'Overall', '08099', '37.9514657', '-102.3844108')
('CO', 'Hinsdale County', 'County', None, 'Overall', 'American Indian or Alaska Native', '08053', '37.83084464', '-107.3018567')
('AK', 'Anchorage', 'County', '360.8', 'Female', 'Black', '02020', '61.15914453', '-149.1045591')
('IA', 'Iowa', 'State', '131.5', 'Female', 'Hispanic', '19', '42.076', '-93.5022')
('AR', 'Lonoke County', 'County', '294.7', 'Female', '

In [4]:
# Set the SQL query statement
query = "SELECT * FROM clean_Heart_Disease"

# Execute the query and read the results into a DataFrame
heartdisease_df = pd.read_sql_query(query, conn)

# Display the DataFrame
print(heartdisease_df.head())

  State           LocationDesc GeographicLevel  \
0    AK        Kenai Peninsula          County   
1    AL          Walker County          County   
2    AL       St. Clair County          County   
3    AR            Yell County          County   
4    AS  American Samoa County          County   

  Data Value (Per 100,000 Population)   Gender Race/Ethnicity LocationID  \
0                               165.1     Male       Hispanic      02122   
1                                 109  Overall       Hispanic      01127   
2                                  90  Overall          Asian      01115   
3                                None   Female          Asian      05149   
4                                None     Male          Black      60000   

       Latitude     Longitude  
0   60.19326297  -150.2807443  
1   33.81022639  -87.29707047  
2   33.71606539  -86.31496031  
3   35.00586398  -93.40167591  
4  -14.30175426  -170.7194738  


In [5]:


# heartdisease_df = heartdisease_df.dropna(subset=['None'])

# heartdisease_df = heartdisease_df.

heartdisease_df = heartdisease_df[heartdisease_df['Data Value (Per 100,000 Population)'].notnull()]

print(heartdisease_df.head())


  State      LocationDesc GeographicLevel Data Value (Per 100,000 Population)  \
0    AK   Kenai Peninsula          County                               165.1   
1    AL     Walker County          County                                 109   
2    AL  St. Clair County          County                                  90   
5    FL       Polk County          County                               180.2   
6    GA    Forsyth County          County                               133.5   

    Gender Race/Ethnicity LocationID     Latitude     Longitude  
0     Male       Hispanic      02122  60.19326297  -150.2807443  
1  Overall       Hispanic      01127  33.81022639  -87.29707047  
2  Overall          Asian      01115  33.71606539  -86.31496031  
5   Female       Hispanic      12105   27.9460498  -81.69939066  
6  Overall          Asian      13117   34.2283909  -84.12468503  


In [6]:
# change the data value column to float to make sure it works later in our map
heartdisease_df['Data Value (Per 100,000 Population)'] = pd.to_numeric(heartdisease_df['Data Value (Per 100,000 Population)'], errors='coerce')

heartdisease_df.dtypes

State                                   object
LocationDesc                            object
GeographicLevel                         object
Data Value (Per 100,000 Population)    float64
Gender                                  object
Race/Ethnicity                          object
LocationID                              object
Latitude                                object
Longitude                               object
dtype: object

In [ ]:
# Load the GeoJSON data
geojson_counties = {}

with open('../Resources/counties.geojson', 'r') as file:
    geojson_counties = json.load(file)

print(geojson_counties)

{}


In [10]:
# Create a Folium map centered around the US
m = folium.Map(location=[37.8, -96], zoom_start=4)

# Define a function to style the GeoJSON layer
def style_function(feature):
    county_id = feature['properties']['GEOID']  # Extract the GEOID as county_id
    
    # Filter the DataFrame for the specific county_id and Gender = "Overall"
    overall_county = heartdisease_df[(heartdisease_df['LocationID'] == county_id) & (heartdisease_df['Gender'] == 'Overall')]
    
    if not overall_county.empty:
        # Get the mortality rate from the filtered DataFrame
        mortality_rate = overall_county['Data Value (Per 100,000 Population)'].values[0]
        
        # Define color based on mortality rate
        if mortality_rate > 500:
            fill_color = '#000004'  
        elif mortality_rate > 450:
            fill_color = '#320a5e'  
        elif mortality_rate > 400:
            fill_color = '#781c6d'  
        elif mortality_rate > 300:
            fill_color = '#bc3754'  
        elif mortality_rate > 200:
            fill_color = '#ed6925'  
        elif mortality_rate > 100:
            fill_color = '#fbb61a'  
        else:
            fill_color = '#fcffa4'  
    else:
        fill_color = '#ffffff'  # Default color for counties with no data

    return {
        'fillColor': fill_color,
        'color': 'black',
        'weight': 1,
        'fillOpacity': 0.6,
    }

# Add the GeoJSON layer to the map
folium.GeoJson(
    geojson_counties,
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(
        fields=['NAME'],  # Only include county name here
        aliases=['County:']
    )
).add_to(m)

# Add a custom tooltip with mortality rate
# the tooltip is pulling from the geojson_counties which doesn't have mortality rate (that's in overall_county) so we have to use a for loop below to add in the mortality rate
for feature in geojson_counties['features']:
    county_id = feature['properties']['GEOID']
    overall_county = heartdisease_df[(heartdisease_df['LocationID'] == county_id) & (heartdisease_df['Gender'] == 'Overall')]
    
    if not overall_county.empty:
        mortality_rate = overall_county['Data Value (Per 100,000 Population)'].values[0]
        feature['properties']['Mortality Rate'] = mortality_rate
    else:
        feature['properties']['Mortality Rate'] = 'No Data'

# Update the GeoJson with the new tooltip
folium.GeoJson(
    geojson_counties,
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(
        fields=['NAME', 'Mortality Rate'],  # Now includes mortality rate
        aliases=['County:', 'Mortality Rate (per 100,000):']
    )
).add_to(m)

# Save the map to an HTML file
m.save('../Media/county_overall_map.html')

In [11]:
# repeating the code above and editing the criteria to display male only
# Create a Folium map centered around the US
male_map = folium.Map(location=[37.8, -96], zoom_start=4)

# Define a function to style the GeoJSON layer
def style_function(feature):
    county_id = feature['properties']['GEOID']  # Extract the GEOID as county_id
    
    # Filter the DataFrame for the specific county_id and Gender = "Male"
    male_county = heartdisease_df[(heartdisease_df['LocationID'] == county_id) & (heartdisease_df['Gender'] == 'Male')]
    
    if not male_county.empty:
        # Get the mortality rate from the filtered DataFrame
        m_mortality_rate = male_county['Data Value (Per 100,000 Population)'].values[0]
        
        # Define color based on mortality rate
        if m_mortality_rate > 500:
            fill_color = '#000004'  
        elif m_mortality_rate > 450:
            fill_color = '#320a5e'  
        elif m_mortality_rate > 400:
            fill_color = '#781c6d'  
        elif m_mortality_rate > 300:
            fill_color = '#bc3754'  
        elif m_mortality_rate > 200:
            fill_color = '#ed6925'  
        elif m_mortality_rate > 100:
            fill_color = '#fbb61a'  
        else:
            fill_color = '#fcffa4'  
    else:
        fill_color = '#ffffff'  # Default color for counties with no data

    return {
        'fillColor': fill_color,
        'color': 'black',
        'weight': 1,
        'fillOpacity': 0.6,
    }

# Add the GeoJSON layer to the map
folium.GeoJson(
    geojson_counties,
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(
        fields=['NAME'],  # Only include county name here
        aliases=['County:']
    )
).add_to(male_map)

# Add a custom tooltip with mortality rate
for feature in geojson_counties['features']:
    county_id = feature['properties']['GEOID']
    male_county = heartdisease_df[(heartdisease_df['LocationID'] == county_id) & (heartdisease_df['Gender'] == 'Male')]
    
    if not male_county.empty:
        m_mortality_rate = male_county['Data Value (Per 100,000 Population)'].values[0]
        feature['properties']['Mortality Rate'] = m_mortality_rate
    else:
        feature['properties']['Mortality Rate'] = 'No Data'

# Update the GeoJson with the new tooltip
folium.GeoJson(
    geojson_counties,
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(
        fields=['NAME', 'Mortality Rate'],  # Now includes mortality rate
        aliases=['County:', 'Mortality Rate (per 100,000):']
    )
).add_to(male_map)

# Save the map to an HTML file
male_map.save('../Media/county_male_map.html')

In [12]:
# repeating the code above and editing the criteria to display male only
# Create a Folium map centered around the US
female_map = folium.Map(location=[37.8, -96], zoom_start=4)

# Define a function to style the GeoJSON layer
def style_function(feature):
    county_id = feature['properties']['GEOID']  # Extract the GEOID as county_id
    
    # Filter the DataFrame for the specific county_id and Gender = "Male"
    female_county = heartdisease_df[(heartdisease_df['LocationID'] == county_id) & (heartdisease_df['Gender'] == 'Female')]
    
    if not female_county.empty:
        # Get the mortality rate from the filtered DataFrame
        f_mortality_rate = female_county['Data Value (Per 100,000 Population)'].values[0]
        
        # Define color based on mortality rate
        if f_mortality_rate > 500:
            fill_color = '#000004'  
        elif f_mortality_rate > 450:
            fill_color = '#320a5e'  
        elif f_mortality_rate > 400:
            fill_color = '#781c6d'  
        elif f_mortality_rate > 300:
            fill_color = '#bc3754'  
        elif f_mortality_rate > 200:
            fill_color = '#ed6925'  
        elif f_mortality_rate > 100:
            fill_color = '#fbb61a'  
        else:
            fill_color = '#fcffa4'  
    else:
        fill_color = '#ffffff'  # Default color for counties with no data

    return {
        'fillColor': fill_color,
        'color': 'black',
        'weight': 1,
        'fillOpacity': 0.6,
    }

# Add the GeoJSON layer to the map
folium.GeoJson(
    geojson_counties,
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(
        fields=['NAME'],  # Only include county name here
        aliases=['County:']
    )
).add_to(male_map)

# Add a custom tooltip with mortality rate
for feature in geojson_counties['features']:
    county_id = feature['properties']['GEOID']
    female_county = heartdisease_df[(heartdisease_df['LocationID'] == county_id) & (heartdisease_df['Gender'] == 'Female')]
    
    if not female_county.empty:
        f_mortality_rate = female_county['Data Value (Per 100,000 Population)'].values[0]
        feature['properties']['Mortality Rate'] = f_mortality_rate
    else:
        feature['properties']['Mortality Rate'] = 'No Data'

# Update the GeoJson with the new tooltip
folium.GeoJson(
    geojson_counties,
    style_function=style_function,
    tooltip=folium.GeoJsonTooltip(
        fields=['NAME', 'Mortality Rate'],  # Now includes mortality rate
        aliases=['County:', 'Mortality Rate (per 100,000):']
    )
).add_to(female_map)

# Save the map to an HTML file
female_map.save('../Media/county_female_map.html')

In [13]:
# #closing the connection
conn.close()